In [1]:
#!/usr/bin/env python

# AUGMENCON 2

import os
import sys
from sys import platform
from gekko import GEKKO
import datetime

TEE = False

def delete_objective(model, objective, is_maximize=True):
    model._objectives.remove(('maximize ' if is_maximize else 'minimize ') + str(objective))

def main(s_significance_factors, time=None):
    print('s significance factors: {}'.format(s_significance_factors))
    need_print_payoff_table = True
    need_print_solution_table = True
    need_create_payoff_table = True

    time = datetime.datetime.now() if time is None else time
    m = GEKKO(remote=False) #model
    #m.open_folder()
    m.options.SOLVER = 1 # APOPT solver
    m.options.MAX_ITER = 5000
    #m.options.MAX_MEMORY = 6
    m.options.OTOL = 1e-6
    #m.options.REDUCE = 3
    #m.options.NODES = 50
    m.solver_options.append('nlp_maximum_iterations 1000')
    m.solver_options.append('minlp_max_iter_with_int_sol 1000')
    m.solver_options.append('minlp_maximum_iterations 5000')
    m.solver_options.append('objective_convergence_tolerance 1.0e-5')
    m.solver_options.append('constraint_convergence_tolerance 1.0e-5')
    m.solver_options.append('minlp_branch_method 1')
    #nz = 20   # nonzero
    iq = m.Param(1e-13)   # infinitesimal quantity

    xi = (11, 21, 31)
    qi = (112, 122, 132, 113, 123, 133)
    pi = (1122, 1123, 2122, 2123, 3122, 3123, 1132, 1133, 2132, 2133, 3132, 3133)
    yi = zi = (1, 2, 3)
    fi = tuple(range(1, 6))
    ei = tuple(range(2, 6))
    
    s_ = {}
    for i, value in enumerate((19000, 27500, 23100), 1):
        s_[i] = s_significance_factors[i - 1]*value #m.Param(value=value)
    cap = {}
    for i, value in enumerate((23500, 18500, 27600), 1):
        cap[i] = value #m.Param(value=value)
    capm = {}
    for i, value in enumerate((602000, 645, 43), 1):
        capm[i] = value #m.Param(value=value)
    c = {}
    for i, value in enumerate((155, 135, 160), 1):
        c[i] = value #m.Param(value=value)
    o = {}
    for i, value in enumerate((4.3, 3.4, 3.1), 1):
        o[i] = value #m.Param(value=value)
    d = {}
    for i, value in { 11 : 10891,
                      21 : 12229,
                      31 : 7595,
                      112 : 1350,
                      122 : 1120,
                      132 : 1551,
                      113 : 884,
                      123 : 1212,
                      133 : 1405,
                      1122 : 450,
                      1123 : 538,
                      2122 : 378,
                      2123 : 105,
                      3122 : 138,
                      3123 : 184,
                      1132 : 450,
                      1133 : 538,
                      2132 : 378,
                      2133 : 105,
                      3132 : 138,
                      3133 : 184 }.items():
        d[i] = value #m.Param(value=value)
    co = {}
    for i, value in { 11 : 6.04,
                      21 : 6.04,
                      31 : 6.04,
                      112 : 17,
                      122 : 17,
                      132 : 17,
                      113 : 50,
                      123 : 50,
                      133 : 50,
                      1122 : 17,
                      1123 : 50,
                      2122 : 17,
                      2123 : 50,
                      3122 : 17,
                      3123 : 50,
                      1132 : 17,
                      1133 : 50,
                      2132 : 17,
                      2133 : 50,
                      3132 : 17,
                      3133 : 50 }.items():
        co[i] = value #m.Param(value=value)
    tc = {}
    for i, value in enumerate((0.8, 1.2, 1.5), 1):
        tc[i] = value #m.Param(value=value)
    trc = {}
    for i, value in { 12 : 0.9,
                      13 : 0.7,
                      23 : 1.1,
                      22 : 1.0,
                      32 : 1.1,
                      33 : 0.6 }.items():
        trc[i] = value #m.Param(value=value)
    trt = {}
    for i, value in { 12 : 0.17,
                      13 : 0.17,
                      23 : 0.12,
                      22 : 0.4,
                      32 : 0.12,
                      33 : 0.10 }.items():
        trt[i] = value #m.Param(value=value)
    cc = {}
    for i, value in { 11 : 170.5,
                      21 : 148.5,
                      31 : 176 }.items():
        cc[i] = value #m.Param(value=value)
    cct = {}
    for i, value in { 11 : 4,
                      21 : 4,
                      31 : 4 }.items():
        cct[i] = value #m.Param(value=value)
    v = {}
    for i, value in enumerate((35, 60, 90), 1):
        v[i] = value #m.Param(value=value)

    h = 4 #m.Param(value=4)
    D = 57764 #10000 #m.Param(value=56000)
    C2 = 344
    C3 = 43

    x = {}
    for i2, i in enumerate(xi, 1):
        x[i] = m.Var(integer=True, value=int(s_[i2]/2), lb=0, ub=s_[i2])
    total_cap = sum(value for value in cap.values())
    q = {}
    for i in qi:
        q[i] = m.Var(integer=True, value=int(total_cap/2), lb=0, ub=total_cap)
    p = {}
    for i in pi:
        p[i] = m.Var(integer=True, value=int(total_cap/2), lb=0, ub=total_cap)
    y = {}
    for i in yi:
        y[i] = m.Var(integer=True, lb=0, ub=1)
    z = {}
    for i in zi:
        z[i] = m.Var(integer=True, lb=0, ub=1)
    
    f = {}
    for i in fi + (41, 42, 43):
        f[i] = m.Var(lb=0)
    f4 = {}
    # for i in (1, 2, 3):
    #     f4[i] = m.Var(lb=-1e9, ub=1e9)
    
    eps = m.Param(1e-6)
    s = {}
    for i in ei:
        s[i] = m.Var(value=iq, lb=0)
    e = {}
    for i in ei:
        e[i] = m.Param(value=100)

    m.Equation(x[11] <= s_[1]*y[1])
    m.Equation(x[21] <= s_[2]*y[2])
    m.Equation(x[31] <= s_[3]*y[3])
    m.Equation(q[112] + q[113] <= cap[1]*z[1])
    m.Equation(q[122] + q[123] <= cap[2]*z[2])
    m.Equation(q[132] + q[133] <= cap[3]*z[3])
    
    m.Equation(x[11] + x[21] + x[31] == q[112] + q[122] + q[132] + q[113] + q[123] + q[133])
    m.Equation(q[112] == p[1122] + p[1123] )
    m.Equation(q[122] == p[2122] + p[2123] ) 
    m.Equation(q[132] == p[3122] + p[3123] )
    
    m.Equation(q[113] == p[1132] + p[1133])
    m.Equation(q[123] == p[2132] + p[2133])
    m.Equation(q[133] == p[3132] + p[3133])
    
    m.Equation(q[112] >= C2 )
    m.Equation(q[122] >= C2 ) 
    m.Equation(q[132] >= C2 )
    
    m.Equation(q[113] >= C3)
    m.Equation(q[123] >= C3)
    m.Equation(q[133] >= C3)
    
    m.Equation(p[1122] >= C2 )
    m.Equation(p[2122] >= C2 )
    m.Equation(p[3122] >= C2 )
    
    m.Equation(p[1123] >= C3)
    m.Equation(p[2123] >= C3)
    m.Equation(p[3123] >= C3)
    
    m.Equation(p[1132] >= C2 )
    m.Equation(p[2132] >= C2 )
    m.Equation(p[3132] >= C2 )
    
    m.Equation(p[1133] >= C3)
    m.Equation(p[2133] >= C3)
    m.Equation(p[3133] >= C3)

    m.Equation(p[1122] + p[1123] + p[1132] + p[1133] <= cap[1]*z[1])
    m.Equation(p[2122] + p[2123] + p[2132] + p[2133] <= cap[2]*z[2])
    m.Equation(p[3122] + p[3123] + p[3132] + p[3133] <= cap[3]*z[3])

    m.Equation(p[1122] + p[1123] + p[1132] + p[1133] + p[2122] + p[2123] + p[2132] + p[2133] + p[3122] + p[3123] + p[3132] + p[3133] == D)

    m.Equation(f[1] == sum((c[1]*x[11] + c[2]*x[21] + c[3]*x[31],
                            o[1]*y[1] + o[2]*y[2] + o[3]*y[3],
                            (x[11]*y[1] + x[21]*y[2] + x[31]*y[3])*h/2,
                            (tc[1]*x[11]*d[11] + tc[1]*x[21]*d[21] + tc[1]*x[31]*d[31])/capm[1],
                            (tc[2]*(q[112]*d[112] + q[122]*d[122] + q[132]*d[132]))/capm[2],
                            (tc[3]*(q[113]*d[113] + q[123]*d[123] + q[133]*d[133]))/capm[3],
                            (tc[2]*(p[1122]*d[1122]*z[1] + p[2122]*d[2122]*z[2] + p[3122]*d[3122]*z[3]))/capm[2],
                            (tc[2]*(p[1132]*d[1132]*z[1] + p[2132]*d[2132]*z[2] + p[3132]*d[3132]*z[3]))/capm[2],
                            (tc[3]*(p[1123]*d[1123]*z[1] + p[2123]*d[2123]*z[2] + p[3123]*d[3123]*z[3]))/capm[3],
                            (tc[3]*(p[1133]*d[1133]*z[1] + p[2133]*d[2133]*z[2] + p[3133]*d[3133]*z[3]))/capm[3],
                            trc[12]*(q[112] + q[122] + q[132]),
                            trc[13]*(q[113] + q[123] + q[133]),
                            trc[22]*(p[1122]*z[1] + p[2122]*z[2] + p[3122]*z[3]),
                            trc[23]*(p[1123]*z[1] + p[2123]*z[2] + p[3123]*z[3]),
                            trc[32]*(p[1132]*z[1] + p[2132]*z[2] + p[3132]*z[3]),
                            trc[33]*(p[1133]*z[1] + p[2133]*z[2] + p[3133]*z[3]),
                            cc[11]*x[11]*y[1] + cc[21]*x[21]*y[2] + cc[31]*x[31]*y[3])))
    m.Equation(f[2] == sum(((x[11]*d[11] + x[21]*d[21] + x[31]*d[31])/(v[1]*capm[1]),
                            (q[112]*d[112]*z[1] + q[122]*d[122]*z[2] + q[132]*d[132]*z[3])/(v[2]*capm[2]),
                            (q[113]*d[113]*z[1] + q[123]*d[123]*z[2] + q[133]*d[133]*z[3])/(v[3]*capm[3]),
                            (p[1122]*d[1122]*z[1] + p[2122]*d[2122]*z[2] + p[3122]*d[3122]*z[3])/(v[2]*capm[2]),
                            (p[1132]*d[1132]*z[1] + p[2132]*d[2132]*z[2] + p[3132]*d[3132]*z[3])/(v[2]*capm[2]),
                            (p[1123]*d[1123]*z[1] + p[2123]*d[2123]*z[2] + p[3123]*d[3123]*z[3])/(v[3]*capm[3]),
                            (p[1133]*d[1133]*z[1] + p[2133]*d[2133]*z[2] + p[3133]*d[3133]*z[3])/(v[3]*capm[3]),
                            trt[12]*(q[112] + q[122] + q[132])/capm[2],
                            trt[13]*(q[113] + q[123] + q[133])/capm[3],
                            trt[22]*(p[1122]*z[1] + p[2122]*z[2] + p[3122]*z[3])/capm[2],
                            trt[23]*(p[1123]*z[1] + p[2123]*z[2] + p[3123]*z[3])/capm[3],
                            trt[32]*(p[1132]*z[1] + p[2132]*z[2] + p[3132]*z[3])/capm[2],
                            trt[33]*(p[1133]*z[1] + p[2133]*z[2] + p[3133]*z[3])/capm[3],
                            (cct[11]*x[11]*y[1] + cct[21]*x[21]*y[2] + cct[31]*x[31]*y[3])/capm[1])))
    m.Equation(f[3] == sum(((co[11]*d[11]*x[11] + co[21]*d[21]*x[21] + co[31]*d[31]*x[31])/capm[1],
                            (co[112]*d[112]*q[112]*z[1] + co[122]*d[122]*q[122]*z[2] + co[132]*d[132]*q[132]*z[3])/capm[2],
                            (co[113]*d[113]*q[113]*z[1] + co[123]*d[123]*q[123]*z[2] + co[133]*d[133]*q[133]*z[3])/capm[3],
                            (co[1122]*d[1122]*p[1122]*z[1] + co[2122]*d[2122]*p[2122]*z[2] + co[3122]*d[3122]*p[3122]*z[3])/capm[2],
                            (co[1132]*d[1132]*p[1132]*z[1] + co[2132]*d[2132]*p[2132]*z[2] + co[3132]*d[3132]*p[3132]*z[3])/capm[2],
                            (co[1123]*d[1123]*p[1123]*z[1] + co[2123]*d[2123]*p[2123]*z[2] + co[3123]*d[3123]*p[3123]*z[3])/capm[3],
                            (co[1133]*d[1133]*p[1133]*z[1] + co[2133]*d[2133]*p[2133]*z[2] + co[3133]*d[3133]*p[3133]*z[3])/capm[3])))
    f4[1] = m.Intermediate(((73.71+(10*m.log(iq + (d[11]*y[1]+d[21]*y[2]+d[31]*y[3])/v[1])))+(10*m.log(iq + (x[11]+x[21]+x[31])/capm[1])))*((d[11]*y[1]+d[21]*y[2]+d[31]*y[3])/v[1]))
    f4[2] = m.Intermediate(51.518 + 10*m.log(iq + (d[112]*z[1] + d[122]*z[2] + d[132]*z[3] + d[1122]*z[1] + d[2122]*z[2] + d[3122]*z[3] + d[1132]*z[1] + d[2132]*z[2] + d[3132]*z[3])/v[2])*((q[112] + q[122] + q[132] + p[1122] + p[2122] + p[3122] + p[1132] + p[2132] + p[3132])/capm[2]))
    f4[3] = m.Intermediate(210.576*((d[113] + d[123] + d[133] + d[1123] + d[2123] + d[3123] + d[1133] + d[2133] + d[3133])/v[3])*((q[113] + q[123] + q[133] + p[1123] + p[2123] + p[3123] + p[1133] + p[2133] + p[3133])/capm[3]))
    # f4[1] = m.Intermediate((76.06 + 10*m.log(iq + (x[11]*y[1] + x[21]*y[2] + x[31]*y[3])/capm[1]))*(d[11]*y[1] + d[21]*y[2] + d[31]*y[3])/v[1])
    # f4[2] = m.Intermediate(94.145 - 0.56*m.log(iq + (z[1]*(d[112] + d[1122] + d[1132]) + z[2]*(d[122] + d[2122] + d[2132]) + z[3]*(d[132] + d[3122] + d[3132]))/v[2])*((q[112] + q[122] + q[132] + p[1122] + p[2122] + p[3122] + p[1132] + p[2132] + p[3132])/capm[2]))
    # f4[3] = m.Intermediate((10*m.log(iq + (z[1]*(q[113] + p[1123] + p[1133]) + z[2]*(q[123] + p[2123] + p[2133]) + z[3]*(q[133] + p[3123] + p[3133]))/capm[3])/v[3] + 13.1295)*((z[1]*(d[113] + d[1123] + d[1133]) + z[2]*(d[123] + d[2123] + d[2133]) + z[3]*(d[133] + d[3123] + d[3133]))/v[3]))
    m.Equation(f[4] == f4[1] + f4[2] + f4[3])
    # m.Equation(f[4] == f4[1] + f4[2] + f4[3])
    # m.Equation(f[4] == sum((f4[1],
    #                         f4[2],
    #                         f4[3],
    #                          )))
    # m.Equation(f[4] == sum(((76.06 + 10*m.log(iq + (x[11]*y[1] + x[21]*y[2] + x[31]*y[3])/capm[1]))*(d[11]*y[1] + d[21]*y[2] + d[31]*y[3])/v[1],
    #                         94.145 - 0.56*m.log(iq + (z[1]*(d[112] + d[1122] + d[1132]) + z[2]*(d[122] + d[2122] + d[2132]) + z[3]*(d[132] + d[3122] + d[3132]))/v[2])*((q[112] + q[122] + q[132] + p[1122] + p[2122] + p[3122] + p[1132] + p[2132] + p[3132])/capm[2]),
    #                         (10*m.log(iq + (z[1]*(q[113] + p[1123] + p[1133]) + z[2]*(q[123] + p[2123] + p[2133]) + z[3]*(q[133] + p[3123] + p[3133]))/capm[3])/v[3] + 13.1295)*((z[1]*(d[113] + d[1123] + d[1133]) + z[2]*(d[123] + d[2123] + d[2133]) + z[3]*(d[133] + d[3123] + d[3133]))/v[3]),
    #                          )))
    #m.Equation(f[5] == 0.15*x[11] + 0.17*x[21] + 0.11*x[31])
    m.Equation(f[5] == (0.08*x[11] + 0.07*x[21] + 0.11*x[31]) + (0.04*x[11] + 0.06*x[21] + 0.03*x[31]) + (0.04*x[11] + 0.05*x[21] + 0.03*x[31]))

    dir_name = 'AUG_II_results'
    if not os.path.exists(dir_name):
        os.makedirs(dir_name)

    #payoff table
    if need_create_payoff_table:
        pt = {}
        is_all_function_solved = True
        for i in range(1, 6):
            of = getattr(m, 'Maximize' if i > 3 else 'Minimize')(f[i])
            try:
                m.solve()
            except Exception as ex:
                is_all_function_solved = False
                print('f[%s] solving error: %s' % (i, ex))
                continue
            finally:
                delete_objective(m, f[i], i > 3)
            print('{} f{} = {}'.format('max' if i > 3 else 'min', i, f[i].value[0]))
            pt[i] = dict((j, f[j].value[0]) for j in range(1, 6))
        if not is_all_function_solved:
            print('There are unsolved functions')
            return
        print('Payoff table is created')
        with open('{0}/payoff_table_ssf{2}_{1:%Y%m%d%H%M%S}.csv'.format(dir_name, time, ''.join('%d' % f for f in s_significance_factors)), 'w') as ptf:
            headers = ('min/max f',) + tuple('f%s' % i for i in fi)
            ptf.write(';'.join(headers) + '\n')
            for i in fi:
                ptf.write('f%s;' % i)
                ptf.write(';'.join('{:.4f}'.format(value) for value in tuple(pt[i][j] for j in fi)) + '\n')

        if need_print_payoff_table:
            headers = ('{:>10}'.format('min/max f'),) + tuple(('{:>10}' if k > 0 else '{:>17}').format('f%s' % i) for k, i in enumerate(fi))
            print(' '.join(headers))
            for i in fi:
                print('{:10} '.format('f%s' % i) + ' '.join(('{:10.4f}' if k > 0 else '{:17.4f}').format(value) for k, value in enumerate(pt[i][j] for j in fi)))


    r = {}
    flb = {}
    for i in range(2, 6):
        v = tuple(pt[j][i] for j in range(1, 6))
        flb[i] = min(v)
        r[i] = max(v) - flb[i]
    print('flb=%s' % flb)
    print('r=%s' % r)
    
    of1 = m.Maximize(-f[1] - eps*sum(10**-(i - 2)*(s[i]/r[i]) for i in range(2, 4)) + eps*(1e-3*s[4]/r[4] + 1e-4*s[5]/r[5]))
    for i in range(2, 6):
        m.Equation((f[i] - s[i]) == e[i])


    #n = int(sys.argv[1]) if sys.argv[1] else 2   # intervals number
    n = 2   # intervals number
    print('Intervals number=%s' % n)
    solutions = []
    dir_name = 'AUG_II_results'
    if not os.path.exists(dir_name):
        os.makedirs(dir_name)
    with open('{0}/solution_in{1}_ssf{3}_{2:%Y%m%d%H%M%S}.csv'.format(dir_name, n, time, ''.join('%d' % f for f in s_significance_factors)), 'w') as sf:
        headers = (tuple('f%s' % i for i in fi) +
                   tuple('x%s' % i for i in xi) +
                   tuple('p%s' % i for i in pi) +
                   tuple('q%s' % i for i in qi) +
                   tuple('y%s' % i for i in yi) +
                   tuple('z%s' % i for i in zi) +
                   tuple('e%s' % i for i in ei) +
                   tuple('f4.%s' % i for i in range(1, 4)))
        sf.write(';'.join(headers) + '\n')
        for i5 in range(0, n + 1):
            e[5].value = flb[5] + i5*(1/n)*r[5]
            for i4 in range(0, n + 1):
                e[4].value = flb[4] + i4*(1/n)*r[4]
                for i3 in range(0, n + 1):
                    e[3].value = flb[3] + i3*(1/n)*r[3]
                    i2 = 0
                    while i2 <= n:
                        e[2].value = flb[2] + i2*(1/n)*r[2]
                        print('f5 index={}, f4 index={}, f3 index={}, f2 index={}'.format(i5, i4, i3, i2))
                        print(', '.join('e%s=%s' % (k, e.value) for k, e in e.items()))
                        try:
                            m.solve()
                            status = m.options.SOLVESTATUS
                        except Exception:
                            status = 0
                        if not status:
                            break
                        sol = dict(tuple(('f%s' % i, f[i].value[0]) for i in fi) +
                                        tuple(('x%s' % i, x[i].value[0]) for i in xi) +
                                        tuple(('p%s' % i, p[i].value[0]) for i in pi) +
                                        tuple(('q%s' % i, q[i].value[0]) for i in qi) +
                                        tuple(('y%s' % i, y[i].value[0]) for i in yi) +
                                        tuple(('z%s' % i, z[i].value[0]) for i in zi) +
                                        tuple(('e%s' % i, e[i].value[0]) for i in ei) +
                                        tuple(('f4.%s' % i, f4[i].value[0]) for i in range(1, 4)))
                        solutions.append(sol)
                        values = (tuple(sol['f%s' % i] for i in fi) +
                                    tuple(sol['x%s' % i] for i in xi) +
                                    tuple(sol['p%s' % i] for i in pi) +
                                    tuple(sol['q%s' % i] for i in qi) +
                                    tuple(sol['y%s' % i] for i in yi) +
                                    tuple(sol['z%s' % i] for i in zi) +
                                    tuple(sol['e%s' % i] for i in ei) +
                                    tuple(sol['f4.%s' % i] for i in range(1, 4)))
                        sf.write(';'.join('{:.4f}'.format(value) for value in values) + '\n')
                        sf.flush()
                            #print('s[2]={}, r[2]={}'.format(s[2].value[0], r[2]))
                        i2 += max(1, int(n*s[2].value[0]/r[2]) if r[2] else 0)# if r[2] != 0 else n + 1
        print('Solution table is created')
        
        if need_print_solution_table:
            headers = (('{:>10}' if i > 0 else '{:>17}').format(h)
                       for i, h in enumerate((tuple('f%s' % i for i in fi) +
                                              tuple('x%s' % i for i in xi) +
                                              tuple('p%s' % i for i in pi) +
                                              tuple('q%s' % i for i in qi) +
                                              tuple('y%s' % i for i in yi) +
                                              tuple('z%s' % i for i in zi) +
                                              tuple('e%s' % i for i in ei))))
            print(' '.join(headers))
            for s in solutions:
                values = (tuple(s['f%s' % i] for i in fi) +
                          tuple(s['x%s' % i] for i in xi) +
                          tuple(s['p%s' % i] for i in pi) +
                          tuple(s['q%s' % i] for i in qi) +
                          tuple(s['y%s' % i] for i in yi) +
                          tuple(s['z%s' % i] for i in zi) +
                          tuple(s['e%s' % i] for i in ei))
                print(' '.join(('{:10.4f}' if i > 0 else '{:17.4}').format(v) for i, v in enumerate(values)))

if __name__ == '__main__':
    time = datetime.datetime.now()
    #for i in range(1, 8):
    for i in range(7, 8):
        main((i & 1, i >> 1 & 1, i >> 2 & 1), time)


s significance factors: (1, 1, 1)
 ----------------------------------------------------------------
 APMonitor, Version 0.9.2
 APMonitor Optimization Suite
 ----------------------------------------------------------------
 
 
 --------- APM Model Size ------------
 Each time step contains
   Objects      :  0
   Constants    :  0
   Variables    :  72
   Intermediates:  3
   Connections  :  0
   Equations    :  44
   Residuals    :  41
 
 Number of state variables:    66
 Number of total equations: -  40
 Number of slack variables: -  27
 ---------------------------------------
 Degrees of freedom       :    -1
 
 * Warning: DOF <= 0
 ----------------------------------------------
 Steady State Optimization with APOPT Solver
 ----------------------------------------------
Iter:     1 I:  0 Tm:      0.03 NLPi:   14 Dpth:    0 Lvs:    3 Obj:  1.67E+07 Gap:       NaN
--Integer Solution:   1.83E+07 Lowest Leaf:   1.67E+07 Gap:   8.67E-02
Iter:     2 I:  0 Tm:      0.00 NLPi:    4 Dpth:    

 ----------------------------------------------------------------
 APMonitor, Version 0.9.2
 APMonitor Optimization Suite
 ----------------------------------------------------------------
 
 
 --------- APM Model Size ------------
 Each time step contains
   Objects      :  0
   Constants    :  0
   Variables    :  72
   Intermediates:  3
   Connections  :  0
   Equations    :  44
   Residuals    :  41
 
 Number of state variables:    66
 Number of total equations: -  40
 Number of slack variables: -  27
 ---------------------------------------
 Degrees of freedom       :    -1
 
 * Warning: DOF <= 0
 ----------------------------------------------
 Steady State Optimization with APOPT Solver
 ----------------------------------------------
Iter:     1 I:  0 Tm:      0.01 NLPi:    7 Dpth:    0 Lvs:    3 Obj:  2.42E+03 Gap:       NaN
--Integer Solution:   2.90E+03 Lowest Leaf:   2.42E+03 Gap:   1.82E-01
Iter:     2 I:  0 Tm:      0.01 NLPi:    5 Dpth:    1 Lvs:    2 Obj:  2.90E+03 Gap:  1

 ----------------------------------------------------------------
 APMonitor, Version 0.9.2
 APMonitor Optimization Suite
 ----------------------------------------------------------------
 
 
 --------- APM Model Size ------------
 Each time step contains
   Objects      :  0
   Constants    :  0
   Variables    :  72
   Intermediates:  3
   Connections  :  0
   Equations    :  44
   Residuals    :  41
 
 Number of state variables:    66
 Number of total equations: -  40
 Number of slack variables: -  27
 ---------------------------------------
 Degrees of freedom       :    -1
 
 * Warning: DOF <= 0
 ----------------------------------------------
 Steady State Optimization with APOPT Solver
 ----------------------------------------------
Iter:     1 I:  0 Tm:      0.00 NLPi:    6 Dpth:    0 Lvs:    3 Obj:  3.46E+06 Gap:       NaN
Iter:     2 I: -1 Tm:      0.01 NLPi:   17 Dpth:    1 Lvs:    2 Obj:  3.46E+06 Gap:       NaN
Iter:     3 I:  0 Tm:      0.00 NLPi:    3 Dpth:    1 Lvs:    4

 ----------------------------------------------------------------
 APMonitor, Version 0.9.2
 APMonitor Optimization Suite
 ----------------------------------------------------------------
 
 
 --------- APM Model Size ------------
 Each time step contains
   Objects      :  0
   Constants    :  0
   Variables    :  72
   Intermediates:  3
   Connections  :  0
   Equations    :  48
   Residuals    :  45
 
 Number of state variables:    66
 Number of total equations: -  44
 Number of slack variables: -  27
 ---------------------------------------
 Degrees of freedom       :    -5
 
 * Warning: DOF <= 0
 ----------------------------------------------
 Steady State Optimization with APOPT Solver
 ----------------------------------------------
Iter:     1 I:  0 Tm:      0.01 NLPi:    8 Dpth:    0 Lvs:    3 Obj:  1.68E+07 Gap:       NaN
--Integer Solution:   1.83E+07 Lowest Leaf:   1.68E+07 Gap:   8.97E-02
Iter:     2 I:  0 Tm:      0.00 NLPi:    4 Dpth:    1 Lvs:    2 Obj:  1.83E+07 Gap:  8

 ----------------------------------------------------------------
 APMonitor, Version 0.9.2
 APMonitor Optimization Suite
 ----------------------------------------------------------------
 
 
 --------- APM Model Size ------------
 Each time step contains
   Objects      :  0
   Constants    :  0
   Variables    :  72
   Intermediates:  3
   Connections  :  0
   Equations    :  48
   Residuals    :  45
 
 Number of state variables:    66
 Number of total equations: -  44
 Number of slack variables: -  27
 ---------------------------------------
 Degrees of freedom       :    -5
 
 * Warning: DOF <= 0
 ----------------------------------------------
 Steady State Optimization with APOPT Solver
 ----------------------------------------------
Iter:     1 I:  0 Tm:      0.01 NLPi:    8 Dpth:    0 Lvs:    3 Obj:  1.81E+07 Gap:       NaN
Iter:     2 I:  0 Tm:      0.01 NLPi:    4 Dpth:    1 Lvs:    5 Obj:  1.96E+07 Gap:       NaN
Iter:     3 I:  0 Tm:      0.00 NLPi:    3 Dpth:    2 Lvs:    7

...

 ----------------------------------------------------------------
 APMonitor, Version 0.9.2
 APMonitor Optimization Suite
 ----------------------------------------------------------------
 
 
 --------- APM Model Size ------------
 Each time step contains
   Objects      :  0
   Constants    :  0
   Variables    :  72
   Intermediates:  3
   Connections  :  0
   Equations    :  48
   Residuals    :  45
 
 Number of state variables:    66
 Number of total equations: -  44
 Number of slack variables: -  27
 ---------------------------------------
 Degrees of freedom       :    -5
 
 * Warning: DOF <= 0
 ----------------------------------------------
 Steady State Optimization with APOPT Solver
 ----------------------------------------------
Iter:     1 I:  0 Tm:      0.00 NLPi:    4 Dpth:    0 Lvs:    3 Obj:  2.02E+07 Gap:       NaN
Iter:     2 I: -1 Tm:      0.01 NLPi:    2 Dpth:    1 Lvs:    2 Obj:  2.02E+07 Gap:       NaN
Iter:     3 I: -1 Tm:      0.01 NLPi:    3 Dpth:    1 Lvs:    1

 ----------------------------------------------------------------
 APMonitor, Version 0.9.2
 APMonitor Optimization Suite
 ----------------------------------------------------------------
 
 
 --------- APM Model Size ------------
 Each time step contains
   Objects      :  0
   Constants    :  0
   Variables    :  72
   Intermediates:  3
   Connections  :  0
   Equations    :  48
   Residuals    :  45
 
 Number of state variables:    66
 Number of total equations: -  44
 Number of slack variables: -  27
 ---------------------------------------
 Degrees of freedom       :    -5
 
 * Warning: DOF <= 0
 ----------------------------------------------
 Steady State Optimization with APOPT Solver
 ----------------------------------------------
Iter:     1 I:  0 Tm:      0.00 NLPi:    5 Dpth:    0 Lvs:    3 Obj:  1.89E+07 Gap:       NaN
Iter:     2 I: -1 Tm:      0.00 NLPi:    3 Dpth:    1 Lvs:    2 Obj:  1.89E+07 Gap:       NaN
Iter:     3 I:  0 Tm:      0.00 NLPi:    3 Dpth:    1 Lvs:    4

 ----------------------------------------------------------------
 APMonitor, Version 0.9.2
 APMonitor Optimization Suite
 ----------------------------------------------------------------
 
 
 --------- APM Model Size ------------
 Each time step contains
   Objects      :  0
   Constants    :  0
   Variables    :  72
   Intermediates:  3
   Connections  :  0
   Equations    :  48
   Residuals    :  45
 
 Number of state variables:    66
 Number of total equations: -  44
 Number of slack variables: -  27
 ---------------------------------------
 Degrees of freedom       :    -5
 
 * Warning: DOF <= 0
 ----------------------------------------------
 Steady State Optimization with APOPT Solver
 ----------------------------------------------
Iter:     1 I:  0 Tm:      0.00 NLPi:    4 Dpth:    0 Lvs:    3 Obj:  2.02E+07 Gap:       NaN
Iter:     2 I: -1 Tm:      0.01 NLPi:    2 Dpth:    1 Lvs:    2 Obj:  2.02E+07 Gap:       NaN
Iter:     3 I: -1 Tm:      0.01 NLPi:    5 Dpth:    1 Lvs:    1

 ----------------------------------------------------------------
 APMonitor, Version 0.9.2
 APMonitor Optimization Suite
 ----------------------------------------------------------------
 
 
 --------- APM Model Size ------------
 Each time step contains
   Objects      :  0
   Constants    :  0
   Variables    :  72
   Intermediates:  3
   Connections  :  0
   Equations    :  48
   Residuals    :  45
 
 Number of state variables:    66
 Number of total equations: -  44
 Number of slack variables: -  27
 ---------------------------------------
 Degrees of freedom       :    -5
 
 * Warning: DOF <= 0
 ----------------------------------------------
 Steady State Optimization with APOPT Solver
 ----------------------------------------------
Iter:     1 I:  0 Tm:      0.00 NLPi:    3 Dpth:    0 Lvs:    3 Obj:  2.02E+07 Gap:       NaN
Iter:     2 I: -1 Tm:      0.00 NLPi:    3 Dpth:    1 Lvs:    2 Obj:  2.02E+07 Gap:       NaN
Iter:     3 I: -1 Tm:      0.00 NLPi:    3 Dpth:    1 Lvs:    1

 ----------------------------------------------------------------
 APMonitor, Version 0.9.2
 APMonitor Optimization Suite
 ----------------------------------------------------------------
 
 
 --------- APM Model Size ------------
 Each time step contains
   Objects      :  0
   Constants    :  0
   Variables    :  72
   Intermediates:  3
   Connections  :  0
   Equations    :  48
   Residuals    :  45
 
 Number of state variables:    66
 Number of total equations: -  44
 Number of slack variables: -  27
 ---------------------------------------
 Degrees of freedom       :    -5
 
 * Warning: DOF <= 0
 ----------------------------------------------
 Steady State Optimization with APOPT Solver
 ----------------------------------------------
Iter:     1 I:  0 Tm:      0.00 NLPi:    3 Dpth:    0 Lvs:    3 Obj:  2.10E+07 Gap:       NaN
Iter:     2 I:  0 Tm:      0.00 NLPi:    2 Dpth:    1 Lvs:    5 Obj:  2.10E+07 Gap:       NaN
--Integer Solution:   2.10E+07 Lowest Leaf:   2.10E+07 Gap:   0